# SWB Connectivity Analysis: Beta Coherence

Created: 08/22/2024 \
Updated: 08/29/2024 \
*using new all_behav data from swb_subj_behav class*


In [1]:
import numpy as np
import mne
from glob import glob
import matplotlib.pyplot as plt
from matplotlib.backends.backend_pdf import PdfPages
import seaborn as sns
from scipy.stats import zscore, linregress, ttest_ind, ttest_rel, ttest_1samp, pearsonr, spearmanr
import pandas as pd
from mne.preprocessing.bads import _find_outliers
import os 
import joblib
import re
import datetime
import scipy
import random
import statsmodels.api as sm
import statsmodels.formula.api as smf
from statsmodels.stats.outliers_influence import variance_inflation_factor
from statsmodels.regression.mixed_linear_model import MixedLM 
from joblib import Parallel, delayed
import pickle
import itertools
import time 
from matplotlib.ticker import StrMethodFormatter


import mne_connectivity
from mne_connectivity import phase_slope_index, seed_target_indices, spectral_connectivity_epochs
# import fooof
# Import plotting functions
# from fooof.plts.spectra import plot_spectrum, plot_spectra
# # Import the FOOOF object
# from fooof import FOOOF
# from fooof import FOOOFGroup

from tqdm import tqdm
from IPython.display import clear_output

from joblib import delayed, Parallel
from statsmodels.stats import multitest
import warnings
warnings.filterwarnings('ignore')
# print('\n'.join(f'{m.__name__}=={m.__version__}' for m in globals().values() if getattr(m, '__version__', None)))

%load_ext autoreload
%autoreload 2



In [2]:
# Specify root directory for un-archived data and results 
base_dir   = '/sc/arion/projects/guLab/Alie/SWB/'
neural_dir = f'{base_dir}ephys_analysis/data/'
save_dir   = f'{base_dir}ephys_analysis/results/beta_coherence/'
os.makedirs(save_dir,exist_ok=True)

script_dir = '/hpc/users/finka03/swb_ephys_analysis/scripts/'
behav_dir  = f'{script_dir}behav/data/'


date = datetime.date.today().strftime('%m%d%Y')
print(date)

# anat_dir   = f'{base_dir}ephys_analysis/recon_labels/'
# behav_dir  = f'{base_dir}swb_behav_models/data/behavior_preprocessed/'


08292024


In [3]:
import sys
sys.path.append(f'{base_dir}ephys_analysis/LFPAnalysis/')

from LFPAnalysis import analysis_utils,oscillation_utils

sys.path.append(f'{script_dir}analysis_notebooks/')

from ieeg_tools import *

sys.path.append(f'{script_dir}behav/')

from behav_utils import *
from swb_subj_behav import *


In [4]:
subj_ids = list(pd.read_excel(f'{base_dir}ephys_analysis/subj_info/SWB_subjects.xlsx', 
                              sheet_name='Usable_Subjects', usecols=[0]).PatientID)
n_subj = len(subj_ids)
# subj_ids


# Load Behav + Elec ROI Data
- all_behav from updated task_dfs and behav_utils formatting
- roi_reref_labels same as usual

In [5]:
# all_behav = pd.read_csv(f'{behav_dir}all_behav.csv') ## this isn't normalized yet 
raw_behav = [pd.read_csv(f'{behav_dir}{subj_id}_task_df.csv') for subj_id in subj_ids]
all_behav,drops_data = format_all_behav(raw_behav,drops_data=True)

all_behav

subj_id  bdi bdi_thresh  Round        RT   TrialOnset  ChoiceOnset  \
0      MS002   14        low      1  2.059852   513.380590   513.390239   
1      MS002   14        low      2  1.954564   522.640856   522.641563   
2      MS002   14        low      3  1.583462   531.174799   531.175599   
3      MS002   14        low      4  2.491611   545.592613   545.593355   
4      MS002   14        low      5  1.768936   555.337336   555.345720   
...      ...  ...        ...    ...       ...          ...          ...   
3840   DA039   22       high    145  1.335964  2251.180979  2251.193149   
3841   DA039   22       high    146  1.079701  2259.827656  2259.828749   
3842   DA039   22       high    147  1.837272  2267.502359  2267.534059   
3843   DA039   22       high    148  4.030006  2282.349445  2282.350662   
3844   DA039   22       high    149  3.167144  2293.040983  2293.042042   

      DecisionOnset  FeedbackOnset ChoicePos  ... choiceEV_t1    rpe_t1  \
0        515.450091     515.457173     right  ...   -0.744531 -0.549717   
1        524.596127     526.627092     right  ...    1.066486  0.948000   
2        532.759061     534.780269     right  ...   -0.090361 -0.008716   
3        548.084966     548.092333      left  ...    0.763502  0.697431   
4        557.114656     559.135069      left  ...   -0.090361 -0.008716   
...             ...            ...       ...  ...         ...       ...   
3840    2252.529113    2254.546404      left  ...    0.889503  0.762497   
3841    2260.908450    2262.926195     right  ...   -0.130463  0.003871   
3842    2269.371331    2269.377701     right  ...   -0.130463  0.003871   
3843    2286.380667    2286.389886      left  ...   -0.130463  0.003871   
3844    2296.209186    2296.218136      left  ...   -1.648269 -1.125038   

      res_type_t1     cf_t1 max_cf_t1    cpe_t1  max_cpe_t1  keep_epoch  \
0      gamble_bad -0.147087  0.020647 -0.452536   -0.456974        keep   
1     gamble_good  0.280945  0.020647  0.724697    0.717387        keep   
2       safe_good -0.452824 -0.382685  0.431913    0.324445        keep   
3     gamble_good  0.342093  0.020647  0.395315    0.520916        keep   
4       safe_good -0.636266 -0.533934  0.614903    0.458402        keep   
...           ...       ...       ...       ...         ...         ...   
3840  gamble_good  0.364301 -0.026383  0.823777    0.722582        keep   
3841    safe_good -1.304944 -0.962934  0.971952    0.645162        keep   
3842     safe_bad  0.373087  0.229608 -0.314481   -0.176344        keep   
3843     safe_bad  0.381872  0.235851 -0.321216   -0.180645        keep   
3844   gamble_bad -0.426394 -0.026383 -1.385385   -1.075270        keep   

      keep_epoch_t1     CpeOnset  
0              keep   517.450091  
1              keep   526.596127  
2              keep   534.759061  
3              keep   550.084966  
4              keep   559.114656  
...             ...          ...  
3840           keep  2254.529113  
3841           keep  2262.908450  
3842           keep  2271.371331  
3843           keep  2288.380667  
3844           keep  2298.209186  

[3845 rows x 56 columns]

In [6]:
roi_reref_labels_master_df = pd.read_csv(
    glob(f'{base_dir}ephys_analysis/results/roi_info/roi_reref_labels_master.csv')[0]).drop(columns=['Unnamed: 0'])

# roi_reref_labels_master_df #= roi_reref_labels_master_df



In [7]:
all_behav.to_csv(f'{save_dir}all_behav_clean_{date}.csv', index=False)

In [ ]:
# #### update all subjects epochs data and resave 
# epoch_id = 'CpeOnset'
# # iterate through subjects
# for subj_id in subj_ids:
#     print(subj_id)
#     # load & format rereferenced epoch data 
#     subj_epochs = mne.read_epochs(f'{neural_dir}{subj_id}/{epoch_id}_epochs.fif', preload=True)
#     # drop bad trials
#     subj_drops = drops_data[subj_id]
#     subj_epochs.drop(subj_drops)
#     # replace old metadata with updated subject data
#     subj_epochs.metadata = all_behav[all_behav.subj_id == subj_id]
#     # save updated epochs data
#     subj_epochs.save(f'{neural_dir}{subj_id}/{epoch_id}_epochs-clean.fif', overwrite=True)
#     del subj_epochs

# Connectivity Computations : Beta Coherence 

In [43]:
# define connectivity analysis parameters:

# spectral parameters - wavelet freqs, wavelet cycles, freq band ranges
freqs = np.logspace(*np.log10([2, 200]), num=30)
n_cycles = np.floor(np.logspace(*np.log10([3, 10]), num=30))

freq_dict = {'theta':[4, 9], 
            'alpha':[9, 13],
            'beta': [13, 30], 
            'hfa': [70, 200]}

# analysis parameters - connectivity metric, conn freq band, num of surrogates for permutations, buffer time in ms
metric   = 'coh'
band     = 'beta' # set band(s) of interest for analysis
n_surr   = 500
buf_ms   = 1000

# data info - analysis epoch + rois for pairwise coh
epoch_id = 'CpeOnset' 
# rois
coh_rois = ['acc','ains','ofc','dlpfc','vlpfc','amy']
# coh_rois = ['ofc','dlpfc','vlpfc','amy']
# dict of subj_ids with elecs in roi 
roi_subj_ids = {f'{roi}':roi_reref_labels_master_df.subj_id[
    roi_reref_labels_master_df.roi == roi].unique().tolist() 
                for roi in coh_rois}
# make unique list of pairs [[pair1,pair2],..] without hard coding 
pairs = [list(tup) for tup in list(itertools.combinations(coh_rois,2))]
pairs

[['acc', 'ains'],
 ['acc', 'ofc'],
 ['acc', 'dlpfc'],
 ['acc', 'vlpfc'],
 ['acc', 'amy'],
 ['ains', 'ofc'],
 ['ains', 'dlpfc'],
 ['ains', 'vlpfc'],
 ['ains', 'amy'],
 ['ofc', 'dlpfc'],
 ['ofc', 'vlpfc'],
 ['ofc', 'amy'],
 ['dlpfc', 'vlpfc'],
 ['dlpfc', 'amy'],
 ['vlpfc', 'amy']]

In [49]:
pairs = pairs[1:]
pairs



[['dlpfc', 'vlpfc'], ['dlpfc', 'amy'], ['vlpfc', 'amy']]

In [ ]:
### resume coherence calculation with remaining pairs 

for pair in pairs:
    
    source_region = pair[0]
    target_region = pair[1]    
    
    # unique pair id roi1_roi2
    pair_id = '_'.join([source_region,target_region])
    
    # find subj with elecs in each roi 
    source_subj = roi_subj_ids[source_region]
    target_subj = roi_subj_ids[target_region]
    # find subj with elecs in both rois
    pair_subj = list(set(source_subj).intersection(target_subj))    
    # save pair subj list 
    
    # initialize the storage list 
    all_subj_pair_df = []
    
    # iterate through pair subjects
    for subj_id in pair_subj:
        
        # load & format rereferenced epoch data 
        subj_epochs = mne.read_epochs(f'{neural_dir}{subj_id}/{epoch_id}_epochs-clean.fif', preload=True)
        subj_elecs  = subj_epochs.ch_names
        
        # construct the seed-to-target mapping based on subject's roi coverage 
        elec_roi_df = roi_reref_labels_master_df[roi_reref_labels_master_df.subj_id==subj_id].reset_index(drop=True)
        # get ch names of subj elecs in roi 
        source_ch_names  = elec_roi_df.reref_ch_names[np.where(elec_roi_df.roi == source_region)[0]].tolist()
        target_ch_names  = elec_roi_df.reref_ch_names[np.where(elec_roi_df.roi == target_region)[0]].tolist()
        # get idx of ch in subj_elecs list (will correspond to idx in epochs array)
        source_elec_idx = [subj_elecs.index(elec) for elec in source_ch_names]
        target_elec_idx = [subj_elecs.index(elec) for elec in target_ch_names]
        # make seed to target indices using mne function 
        seed_to_target = seed_target_indices(
                        source_elec_idx,
                        target_elec_idx)
        
        # elec name for every elec pair 
        subj_pair_ch = list(map(lambda x,y: '_'.join([x,y]), 
                                  [subj_elecs[idx] for idx in  seed_to_target[0]], 
                                  [subj_elecs[idx] for idx in  seed_to_target[1]]))
        # unique elec name for every elec pair 
        unique_ch_pair = list(map(lambda x,y: '_'.join([x,y]), [subj_id]*len(subj_pair_ch), subj_pair_ch))
        
        # compute pwise coherence 
        pwise = oscillation_utils.compute_connectivity(subj_epochs.copy(), 
                                           band = freq_dict[band], 
                                           metric = metric, 
                                           indices = seed_to_target, 
                                           freqs = freqs, 
                                           n_cycles = n_cycles,
                                           buf_ms = buf_ms, 
                                           n_surr=n_surr,
                                           avg_over_dim='time',
                                           band1 = freq_dict[band],
                                           parallelize=True)

        
        coh_df = pd.concat([pd.DataFrame({'epoch':np.arange(0,pwise.shape[0]),'coh':pwise[:,ch_ix],
                                          'unique_ch_pair':[ch_name]*pwise.shape[0],
                                          'roi_pair_chans':['_'.join(ch_name.split('_')[1:])]*pwise.shape[0],
                                          'roi1_ch_names':[ch_name.split('_')[1]]*pwise.shape[0],
                                          'roi2_ch_names':[ch_name.split('_')[2]]*pwise.shape[0],
                                          'roi1_elec_idx':[seed_to_target[0]]*pwise.shape[0],
                                          'roi2_elec_idx':[seed_to_target[1]]*pwise.shape[0]}) 
                            for ch_ix, ch_name in enumerate(unique_ch_pair)])



        coh_df['subj_id']  = subj_id
        coh_df['bdi']      = all_behav[all_behav.subj_id == subj_id].bdi.unique().tolist()[0]
        coh_df['Round']    = all_behav[all_behav.subj_id == subj_id].Round.astype(int)
        coh_df['epoch']    = all_behav[all_behav.subj_id == subj_id].epoch.astype(int)
        coh_df['band']     = band
        coh_df['metric']   = metric
        coh_df['pair_id']  = pair_id
        coh_df['roi1']     = source_region
        coh_df['roi2']     = target_region

        # one pair one subj data 
        coh_df.to_csv(f'{save_dir}{subj_id}_{pair_id}_{metric}_{band}_df.csv')
        all_subj_pair_df.append(coh_df)
        del coh_df, subj_epochs, pwise
#         print(f'finished {subj_id} {pair_id}')
        
    # one pair all subj data 
#     print(f'finished all {pair_id}')
    all_subj_pair_df = pd.concat(all_subj_pair_df).reset_index()
    # save roi pair df separately 
    all_subj_pair_df.to_csv(f'{save_dir}{pair_id}_{metric}_{band}_df.csv', index=False)
    
    del all_subj_pair_df
    

Reading /sc/arion/projects/guLab/Alie/SWB/ephys_analysis/data/MS016/CpeOnset_epochs-clean.fif ...
    Found the data of interest:
        t =   -1000.00 ...    4000.00 ms
        0 CTF compensation matrices available
Adding metadata with 56 columns
135 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 0 - parallel
Not setting metadata
135 matching events found
Computing surrogate # 3 - parallel
Not setting metadata
135 matching events found
Computing surrogate # 2 - parallel
Not setting metadata
135 matching events found
Computing surrogate # 1 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
0 projection items activated
No baseline correction applied
0 projection items activated
No baseline correction applied
0 projection items activated
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 135 events (all good), -1 – 4 s (baseline off), ~167.6 MB, data loaded,
 'CpeOnset': 135>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 135 events (all good), -1 – 4 s (baseline off), ~167.6 MB, data loaded,
 'CpeOnset': 135>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 135 events (all good), -1 – 4 s (baseline off), ~167.6 MB, data loaded,
 'CpeOnset': 135>, so metadata was not modified.
  sur

Computing surrogate # 4 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 5 - parallel
Not setting metadata
135 matching events found
Computing surrogate # 6 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
No baseline correction applied
0 projection items activated
0 projection items activated
Computing surrogate # 7 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 135 events (all good), -1 – 4 s (baseline off), ~167.6 MB, data loaded,
 'CpeOnset': 135>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 135 events (all good), -1 – 4 s (baseline off), ~167.6 MB, data loaded,
 'CpeOnset': 135>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 135 events (all good), -1 – 4 s (baseline off), ~167.6 MB, data loaded,
 'CpeOnset': 135>, so metadata was not modified.
  sur

Computing surrogate # 8 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 9 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 10 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 11 - parallel
Not setting metadata
135 matching events found
No baseline correction applied
0 projection items activated


...

/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 133 events (all good), -1 – 4 s (baseline off), ~172.7 MB, data loaded,
 'CpeOnset': 133>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,


Computing surrogate # 204 - parallel
Not setting metadata
133 matching events found
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 133 events (all good), -1 – 4 s (baseline off), ~172.7 MB, data loaded,
 'CpeOnset': 133>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,


Computing surrogate # 205 - parallel
Not setting metadata
133 matching events found
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 133 events (all good), -1 – 4 s (baseline off), ~172.7 MB, data loaded,
 'CpeOnset': 133>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,


In [46]:
######## to compute coh after notebook ends in middle of roi pair
# pairs = pairs[-4:]
# pairs
# pair_id = 'ofc_amy'
# pair    = pairs[0]

# source_region = pair[0]
# target_region = pair[1]    

# # unique pair id roi1_roi2
# pair_id = '_'.join([source_region,target_region])

# # find subj with elecs in each roi 
# source_subj = roi_subj_ids[source_region]
# target_subj = roi_subj_ids[target_region]

# # find subj with elecs in both rois
# pair_subj = list(set(source_subj).intersection(target_subj))    
# # find completed subj files
# complete_subj_files = glob(f'{save_dir}*ofc_amy_coh_beta_df.csv')
# complete_subj = [file.split('/')[-1].split('_')[0] for file in complete_subj_files]
# # find subj from pair_subj with no saved data
# incomplete_subj = list(np.setdiff1d(pair_subj, complete_subj)) # should be ['MS027','MS017']

# # initialize the storage list 
# all_subj_pair_df = []

# # run incomplete subj only! 
# for subj_id in incomplete_subj:

#     # load & format rereferenced epoch data 
#     subj_epochs = mne.read_epochs(f'{neural_dir}{subj_id}/{epoch_id}_epochs-clean.fif', preload=True)
#     subj_elecs  = subj_epochs.ch_names

#     # construct the seed-to-target mapping based on subject's roi coverage 
#     elec_roi_df = roi_reref_labels_master_df[roi_reref_labels_master_df.subj_id==subj_id].reset_index(drop=True)
#     # get ch names of subj elecs in roi 
#     source_ch_names  = elec_roi_df.reref_ch_names[np.where(elec_roi_df.roi == source_region)[0]].tolist()
#     target_ch_names  = elec_roi_df.reref_ch_names[np.where(elec_roi_df.roi == target_region)[0]].tolist()
#     # get idx of ch in subj_elecs list (will correspond to idx in epochs array)
#     source_elec_idx = [subj_elecs.index(elec) for elec in source_ch_names]
#     target_elec_idx = [subj_elecs.index(elec) for elec in target_ch_names]
#     # make seed to target indices using mne function 
#     seed_to_target = seed_target_indices(
#                     source_elec_idx,
#                     target_elec_idx)

#     # elec name for every elec pair 
#     subj_pair_ch = list(map(lambda x,y: '_'.join([x,y]), 
#                               [subj_elecs[idx] for idx in  seed_to_target[0]], 
#                               [subj_elecs[idx] for idx in  seed_to_target[1]]))
#     # unique elec name for every elec pair 
#     unique_ch_pair = list(map(lambda x,y: '_'.join([x,y]), [subj_id]*len(subj_pair_ch), subj_pair_ch))

#     # compute pwise coherence 
#     pwise = oscillation_utils.compute_connectivity(subj_epochs.copy(), 
#                                        band = freq_dict[band], 
#                                        metric = metric, 
#                                        indices = seed_to_target, 
#                                        freqs = freqs, 
#                                        n_cycles = n_cycles,
#                                        buf_ms = buf_ms, 
#                                        n_surr=n_surr,
#                                        avg_over_dim='time',
#                                        band1 = freq_dict[band],
#                                        parallelize=True)


#     coh_df = pd.concat([pd.DataFrame({'epoch':np.arange(0,pwise.shape[0]),'coh':pwise[:,ch_ix],
#                                       'unique_ch_pair':[ch_name]*pwise.shape[0],
#                                       'roi_pair_chans':['_'.join(ch_name.split('_')[1:])]*pwise.shape[0],
#                                       'roi1_ch_names':[ch_name.split('_')[1]]*pwise.shape[0],
#                                       'roi2_ch_names':[ch_name.split('_')[2]]*pwise.shape[0],
#                                       'roi1_elec_idx':[seed_to_target[0]]*pwise.shape[0],
#                                       'roi2_elec_idx':[seed_to_target[1]]*pwise.shape[0]}) 
#                         for ch_ix, ch_name in enumerate(unique_ch_pair)])



#     coh_df['subj_id']  = subj_id
#     coh_df['bdi']      = all_behav[all_behav.subj_id == subj_id].bdi.unique().tolist()[0]
#     coh_df['Round']    = all_behav[all_behav.subj_id == subj_id].Round
#     coh_df['epoch']    = all_behav[all_behav.subj_id == subj_id].epoch
#     coh_df['band']     = band
#     coh_df['metric']   = metric
#     coh_df['pair_id']  = pair_id
#     coh_df['roi1']     = source_region
#     coh_df['roi2']     = target_region

#     # one pair one subj data 
#     coh_df.to_csv(f'{save_dir}{subj_id}_{pair_id}_{metric}_{band}_df.csv')
#     all_subj_pair_df.append(coh_df)
#     del coh_df, subj_epochs,pwise

# # add completed subj dfs to concat list 
# for file in complete_subj_files:
#     subj_id = file.split('/')[-1].split('_')[0]
#     coh_df = pd.read_csv(file)
#     all_subj_pair_df.append(coh_df)

# # make pair df 
# all_subj_pair_df = pd.concat(all_subj_pair_df).reset_index()
# # save roi pair df  
# all_subj_pair_df.to_csv(f'{save_dir}{pair_id}_{metric}_{band}_df.csv', index=False)

    

Reading /sc/arion/projects/guLab/Alie/SWB/ephys_analysis/data/MS017/CpeOnset_epochs-clean.fif ...
    Found the data of interest:
        t =   -1000.00 ...    4000.00 ms
        0 CTF compensation matrices available
Adding metadata with 56 columns
148 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 1 - parallel
Not setting metadata
148 matching events found
Computing surrogate # 2 - parallel
Not setting metadata
148 matching events found
Computing surrogate # 0 - parallel
Not setting metadata
148 matching events found
Computing surrogate # 3 - parallel
Not setting metadata
148 matching events found
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 148 events (all good), -1 – 4 s (baseline off), ~155.4 MB, data loaded,
 'CpeOnset': 148>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 148 events (all good), -1 – 4 s (baseline off), ~155.4 MB, data loaded,
 'CpeOnset': 148>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 148 events (all good), -1 – 4 s (baseline off), ~155.4 MB, data loaded,
 'CpeOnset': 148>, so metadata was not modified.
  sur

No baseline correction applied
0 projection items activated
No baseline correction applied
0 projection items activated
No baseline correction applied
0 projection items activated
Computing surrogate # 4 - parallel
Not setting metadata
148 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 5 - parallel
Not setting metadata
148 matching events found
No baseline correction applied
0 projection items activated
Computing surrogate # 6 - parallel
Not setting metadata
148 matching events found
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 148 events (all good), -1 – 4 s (baseline off), ~155.4 MB, data loaded,
 'CpeOnset': 148>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 148 events (all good), -1 – 4 s (baseline off), ~155.4 MB, data loaded,
 'CpeOnset': 148>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 148 events (all good), -1 – 4 s (baseline off), ~155.4 MB, data loaded,
 'CpeOnset': 148>, so metadata was not modified.
  sur

Computing surrogate # 7 - parallel
Not setting metadata
148 matching events found
No baseline correction applied
0 projection items activated


...

/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 145 events (all good), -1 – 4 s (baseline off), ~229.8 MB, data loaded,
 'CpeOnset': 145>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,


Computing surrogate # 498 - parallel
Not setting metadata
145 matching events found
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 145 events (all good), -1 – 4 s (baseline off), ~229.8 MB, data loaded,
 'CpeOnset': 145>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,


Computing surrogate # 499 - parallel
Not setting metadata
145 matching events found
No baseline correction applied
0 projection items activated


/sc/arion/projects/guLab/Alie/SWB/ephys_analysis/LFPAnalysis/LFPAnalysis/oscillation_utils.py:405: RuntimeWarning: There were no Annotations stored in <EpochsArray | 145 events (all good), -1 – 4 s (baseline off), ~229.8 MB, data loaded,
 'CpeOnset': 145>, so metadata was not modified.
  surr_conn = np.squeeze(spectral_connectivity_time(data=surr_mne,
